In [ ]:
#Importing required modules
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer,CountVectorizer
from sklearn.metrics import confusion_matrix
from sklearn import metrics
from sklearn.metrics import roc_curve, auc

import pickle
from tqdm import tqdm
import os

In [ ]:
import warnings
warnings.filterwarnings("ignore") 

In [ ]:
#Uploading Files Temporarity to Google Colab
from google.colab import files
uploaded = files.upload()

Saving processed_data.csv to processed_data.csv


In [ ]:
uploaded

{'processed_data.csv': b'content,intent,File_Name,content1,polarity,content2\r\nin this video as sudhansu sir explains that we are using the softmax function for the classification in the outer layer the formula for softmax is e^x(i)/sum(e^x(i). how did we get the value for these classes? because in the video when sir explained softmax activation function using the dice example it was pretty simple but can you please explain this,activation_function,activation_function.xlsx,video sudhansu sir explains using softmax function classification outer layer formula softmax e x sum e x get value class video sir explained softmax activation function using dice example pretty simple please explain,0.125,video sudhansu sir explains using softmax function classification outer layer formula softmax e x sum e x get value class video sir explained softmax motivation function using dice example pretty simple please explain\r\n"i have some doubts regarding activation function, can you please help me?",

#### Data Loading and Preprocessing

##### Loading Processed data to dataframe

In [ ]:
df_text=pd.read_csv('processed_data.csv')

In [ ]:
print(df_text.shape)
df_text.head()

(24195, 6)


content  ...                                           content2
0  in this video as sudhansu sir explains that we...  ...  video sudhansu sir explains using softmax func...
1  i have some doubts regarding activation functi...  ...    doubt regarding motivation function please help
2  suppose i am using any activation function and...  ...  suppose using motivation function accuracy mod...
3  i know in case vanishing gradient weight of in...  ...  know case vanishing radiant weight inner layer...
4  i am a student of dlcvnlp 25th batch and have ...  ...  student dlcvnlp th batch question related conc...

[5 rows x 6 columns]

Preprocessed data contains:
  - Record Count: 24195
  - Features/Columns: 6

Removing intents with count less than 10

In [ ]:
tmp_dict=(df_text['intent'].value_counts()<10).to_dict()
remove_intent=[key for key in tmp_dict if tmp_dict[key]==True]

In [ ]:
df_text=df_text[~df_text.intent.isin(remove_intent)]

In [ ]:
df_text['intent'].value_counts()

welcome_reply              6298
internship_query           1785
batch_details              1146
user_name                   682
tensorflow_installation     632
                           ... 
cufflinks_installation       18
assignment_knn               18
blog                         16
bot_timing                   15
doubt_session_link           14
Name: intent, Length: 173, dtype: int64

In [ ]:
df_text=df_text.drop('content2', axis=1)

In [ ]:
df_text=df_text.drop('content', axis=1)
df_text.head()

intent  ... polarity
0  activation_function  ...    0.125
1  activation_function  ...    0.000
2  activation_function  ...    0.600
3  activation_function  ...   -0.025
4  activation_function  ...    0.000

[5 rows x 4 columns]

Checking for presence of NULL values in columns.

In [ ]:
df_text.isna().sum()

intent        0
File_Name     0
content1     54
polarity      0
dtype: int64

In [ ]:
#Dropping File Name and NULL Values from content1
df_text=df_text.drop('File_Name', axis=1)
df_text=df_text.dropna(subset=['content1'])

In [ ]:
df_text.isna().sum()

intent      0
content1    0
polarity    0
dtype: int64

In [ ]:
#Final Dataframe Shape
df_text.shape

(24135, 3)

#### Splitting data into test and train dataset

In [ ]:
from sklearn.model_selection import train_test_split

In [ ]:
X=df_text.drop('intent',axis=1)

In [ ]:
X.head()

content1  polarity
0  video sudhansu sir explains using softmax func...     0.125
1    doubt regarding activation function please help     0.000
2  suppose using activation function accuracy mod...     0.600
3  know case vanishing gradient weight inner laye...    -0.025
4  student dlcvnlp th batch question related conc...     0.000

In [ ]:
y=df_text['intent'].values

##### Encoding Intent Values

In [ ]:
from sklearn import preprocessing
le = preprocessing.LabelEncoder()

In [ ]:
le.fit(y)
#print(le.classes_)
y_val=le.transform(y)

In [ ]:
print(y_val, len(y_val))

[  0   0   0 ... 172 172 172] 24135


In [ ]:
len(set(y_val))

173

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X, y_val, test_size=0.25, stratify=y_val)

In [ ]:
set(y_val).union(set(y_test)) - set(y_val).intersection(set(y_test))

set()

#### CountVectorizer

In [ ]:
vectorizer = CountVectorizer(ngram_range=(1,4), min_df=5)

In [ ]:
vectorizer.fit(X_train['content1'].values) # fit has to happen only on train data

CountVectorizer(analyzer='word', binary=False, decode_error='strict',
                dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
                lowercase=True, max_df=1.0, max_features=None, min_df=5,
                ngram_range=(1, 4), preprocessor=None, stop_words=None,
                strip_accents=None, token_pattern='(?u)\\b\\w\\w+\\b',
                tokenizer=None, vocabulary=None)

In [ ]:
# we use the fitted CountVectorizer to convert the text to vector
X_train_content_bow = vectorizer.transform(X_train['content1'].values)
X_test_content_bow = vectorizer.transform(X_test['content1'].values)

In [ ]:
print(X_train_content_bow.shape)
print(X_test_content_bow.shape)

(18101, 4581)
(6034, 4581)


CountVectorizer:


1.   Train Shape: 18101, 4570
2.   Test Shape: 6034, 4570



#### Normalising polarity data

In [ ]:
from sklearn.preprocessing import Normalizer
normalizer = Normalizer()

In [ ]:
X_train_polarity_norm = normalizer.fit_transform(X_train['polarity'].values.reshape(-1,1))
X_test_polarity_norm = normalizer.transform(X_test['polarity'].values.reshape(-1,1))

In [ ]:
print(X_train_polarity_norm.shape)
print(X_test_polarity_norm.shape)

(18101, 1)
(6034, 1)


In [ ]:
print(X_train_polarity_norm.shape, X_train_content_bow.shape)

(18101, 1) (18101, 4581)


In [ ]:
#Combining Bag of words and Polarity Normalised data
from scipy.sparse import hstack
X_train_bow = hstack((X_train_polarity_norm,X_train_content_bow)).tocsr()
X_test_bow = hstack((X_test_polarity_norm,X_test_content_bow)).tocsr()

In [ ]:
X_train_bow.shape

(18101, 4582)

#### TFIDF Vectorizer

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer

In [ ]:
tfvec = TfidfVectorizer(min_df=5, ngram_range=(1,4))

In [ ]:
tfvec.fit(X_train['content1'].values) # fit has to happen only on train data
# we use the fitted TFIDFVectoizer to convert the text to vector
X_train_content_tfidf = tfvec.transform(X_train['content1'].values)
X_test_content_tfidf = tfvec.transform(X_test['content1'].values)

In [ ]:
print(X_train_content_tfidf.shape)
print(X_test_content_tfidf.shape)

(18101, 4581)
(6034, 4581)


TF-IDF:


1.   Train Shape: 18101, 4570
2.   Test Shape: 6034, 4570


In [ ]:
X_train_tfidf = hstack((X_train_polarity_norm,X_train_content_tfidf)).tocsr()
X_test_tfidf = hstack((X_test_polarity_norm,X_test_content_tfidf)).tocsr()

In [ ]:
print(X_train_polarity_norm.shape,type(X_train_polarity_norm))
print(X_train_content_tfidf.shape,type(X_train_content_tfidf))

(18101, 1) <class 'numpy.ndarray'>
(18101, 4581) <class 'scipy.sparse.csr.csr_matrix'>


In [ ]:
from sklearn.multiclass import OneVsRestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier

In [ ]:
pip install xgboost

In [ ]:
import xgboost as xgb
from sklearn.model_selection import GridSearchCV,RandomizedSearchCV

In [ ]:
df_pred=pd.DataFrame(columns=['Vectorizer','Model Name','Score','AUC ROC Score'])

In [ ]:
data_list=[]

In [ ]:
#Logistic Regression HyperParams
logistic_params={
    'penalty': ['l1', 'l2', 'elasticnet', None],
    'C': [0.1,1,10,100]
}

In [ ]:
#DecisionTree Regression HyperParams
decisiontree_params={
    'criterion': ['gini','entropy'],
    'splitter': ['best','random'],
    'max_depth': [5,8,10,None],
    'min_samples_split': [2,3,5],
    'min_samples_leaf': [1,3,5,7],
    'max_features': ['auto','sqrt','log2']
}

In [ ]:
#RandonForest Regression HyperParams
randomforest_params={
    'n_estimators': [90,100,110,130,150,170,190],
    'criterion': ['gini','entropy'],
    'max_depth': [5,8,10,None],
    'min_samples_split': [2,3,5],
    'min_samples_leaf': [1,3,5,7],
    'max_features': ['auto','sqrt','log2',None]
}

In [ ]:
#XgBoost Regression HyperParams
xgboost_params={
    'min_child_weight': [1, 5, 10],
    'gamma': [0.5, 1, 1.5, 2, 5],
    'subsample': [0.6, 0.8, 1.0],
    'colsample_bytree': [0.6, 0.8, 1.0],
    'max_depth': [3, 4, 5]
}

In [ ]:
#Logistic Regression Function
def model_logisticregression(train_x,train_y,test_x,test_y):
  log=OneVsRestClassifier(LogisticRegression(n_jobs=-1))
  log.fit(train_x,train_y)
  y_pred=log.predict(test_x)
  log_score=log.score(test_x, test_y)
  print(log_score)
  return log_score

In [ ]:
#DecisionTree Regression Function
def model_decisionregression(train_x,train_y,test_x,test_y):
  decision_tree=DecisionTreeClassifier()
  decision_tree.fit(train_x,train_y)
  y_pred=decision_tree.predict(test_x)
  decision_score=decision_tree.score(test_x, test_y)
  return decision_score

In [ ]:
#RandomForest Regressor
def model_rfregression(train_x,train_y,test_x,test_y):
  rf_model=RandomForestClassifier(n_jobs=-1)
  rf_model.fit(train_x,train_y)
  y_pred=rf_model.predict(test_x)
  rf_score=rf_model.score(test_x, test_y)
  return rf_score

In [ ]:
def model_xgbregression(train_x,train_y,test_x,test_y):
  xgb_model=xgb.XGBClassifier(objective= 'multi:softmax', n_jobs=-1)
  xgb_model.fit(train_x,train_y)
  y_pred=xgb_model.predict(test_x)
  xgb_score=xgb_model.score(test_x, test_y)
  return xgb_score

In [ ]:
def logistic_hyperparams(train_x,train_y,test_x,test_y):
  grid_search=GridSearchCV(LogisticRegression(multi_class='multinomial',solver='lbfgs'),param_grid=logistic_params,verbose=5,return_train_score=True,cv=5,n_jobs=-1)
  grid_search.fit(train_x,train_y)
  params_dict=grid_search.best_params_
  best_score=grid_search.best_score_
  return grid_search,params_dict,best_score

In [ ]:
def decisiontree_hyperparams(train_x,train_y,test_x,test_y):
  grid_search=GridSearchCV(DecisionTreeClassifier(),param_grid=decisiontree_params,verbose=5,return_train_score=True,cv=5,n_jobs=-1)
  grid_search.fit(train_x,train_y)
  params_dict=grid_search.best_params_
  best_score=grid_search.best_score_
  return grid_search,params_dict,best_score

In [ ]:
def rf_hyperparams(train_x,train_y,test_x,test_y):
  grid_search=GridSearchCV(RandomForestClassifier(),param_grid=randomforest_params,verbose=5,return_train_score=True,cv=5,n_jobs=-1)
  grid_search.fit(train_x,train_y)
  params_dict=grid_search.best_params_
  best_score=grid_search.best_score_
  return grid_search,params_dict,best_score

### Building Classifiers - BOW

#### Logistic Regression

In [ ]:
log_bow_score=model_logisticregression(X_train_bow,y_train,X_test_bow,y_test)
print('Logistic Regression BOW: ', log_bow_score)
data_list.append(['Bag Of Words','Logistic Regression',log_bow_score])

0.7833941000994366
Logistic Regression BOW:  0.7833941000994366


##### Logistic GridSearch

In [ ]:
model,params_dict,grid_log_bow_score=logistic_hyperparams(X_train_bow,y_train,X_test_bow,y_test)

Fitting 5 folds for each of 16 candidates, totalling 80 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  41 tasks      | elapsed:  2.4min
[Parallel(n_jobs=-1)]: Done  80 out of  80 | elapsed:  6.1min finished


In [ ]:
print(params_dict,grid_log_bow_score)

{'C': 1, 'penalty': 'l2'} 0.7723885529622323


In [ ]:
data_list.append(['Bag Of Words','Logistic Regression - GridSearch',grid_log_bow_score])

#### DecisionTree Regression

In [ ]:
decision_bow_score=model_decisionregression(X_train_bow,y_train,X_test_bow,y_test)
print('Decision Tree Regression BOW: ', decision_bow_score)
data_list.append(['Bag Of Words','DecisionTree Regression',decision_bow_score])

Decision Tree Regression BOW:  0.7214119986741796


##### Decision GridSearch

In [ ]:
model,params_dict,grid_decision_bow_score=decisiontree_hyperparams(X_train_bow,y_train,X_test_bow,y_test)

Fitting 5 folds for each of 576 candidates, totalling 2880 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  14 tasks      | elapsed:    1.0s
[Parallel(n_jobs=-1)]: Done 392 tasks      | elapsed:    6.4s
[Parallel(n_jobs=-1)]: Done 1112 tasks      | elapsed:   21.9s
[Parallel(n_jobs=-1)]: Done 1378 tasks      | elapsed:   39.6s
[Parallel(n_jobs=-1)]: Done 1974 tasks      | elapsed:   50.7s
[Parallel(n_jobs=-1)]: Done 2620 tasks      | elapsed:  1.2min
[Parallel(n_jobs=-1)]: Done 2880 out of 2880 | elapsed:  1.5min finished


In [ ]:
print('Best Parameters: ',params_dict)
print('Best Score: ',grid_decision_bow_score)
data_list.append(['Bag Of Words','DecisionTree Regression - Grid Search',decision_bow_score])

Best Parameters:  {'criterion': 'gini', 'max_depth': None, 'max_features': 'sqrt', 'min_samples_leaf': 1, 'min_samples_split': 5, 'splitter': 'best'}
Best Score:  0.6504606797975591


#### RandomForest Regression

In [ ]:
rf_bow_score=model_rfregression(X_train_bow,y_train,X_test_bow,y_test)
print('RandomForest Regression BOW: ', rf_bow_score)
data_list.append(['Bag Of Words','RandomForest Regression',rf_bow_score])

RandomForest Regression BOW:  0.7525687769307259


##### RandomForest GridSearch

In [ ]:
model,params_dict,grid_rf_bow_score=rf_hyperparams(X_train_bow,y_train,X_test_bow,y_test)

Fitting 5 folds for each of 2688 candidates, totalling 13440 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done  14 tasks      | elapsed:   23.2s
[Parallel(n_jobs=-1)]: Done  68 tasks      | elapsed:  2.4min
[Parallel(n_jobs=-1)]: Done 158 tasks      | elapsed:  5.5min


In [ ]:
grid_rf_bow_score

#### XGBoost Regression

In [ ]:
xgb_bow_score=model_xgbregression(X_train_bow,y_train,X_test_bow,y_test)
print('XGBoost Regression BOW: ', xgb_bow_score)
data_list.append(['Bag Of Words','XGBoost Regression',xgb_bow_score])

XGBoost Regression BOW:  0.7765992707988068


## Building Classifiers - TFIDF
----

#### Logistic Regression

In [ ]:
log_tfidf_score=model_logisticregression(X_train_tfidf,y_train,X_test_tfidf,y_test)
print('Logistic Regression TFIDF: ', log_tfidf_score)
data_list.append(['TF-IDF','Logistic Regression',log_tfidf_score])

0.7444481272787538
Logistic Regression TFIDF:  0.7444481272787538


#### DecisionTree Regression

In [ ]:
decision_tfidf_score=model_decisionregression(X_train_tfidf,y_train,X_test_tfidf,y_test)
print('Decision Tree Regression TFIDF: ', decision_tfidf_score)
data_list.append(['TF-IDF','DecisionTree Regression',decision_tfidf_score])

Decision Tree Regression TFIDF:  0.7263838249917136


#### RandomForest Regression

In [ ]:
rf_tfidf_score=model_rfregression(X_train_tfidf,y_train,X_test_tfidf,y_test)
print('RandomForest Regression TFIDF: ', rf_tfidf_score)
data_list.append(['TF-IDF','RandomForest Regression',rf_tfidf_score])

RandomForest Regression TFIDF:  0.7621809744779582


#### XGBoost Regression

In [ ]:
xgb_tfidf_score=model_xgbregression(X_train_tfidf,y_train,X_test_tfidf,y_test)
print('XGBoost Regression TFIDF: ', xgb_tfidf_score)
data_list.append(['TF-IDF','XGBoost Regression',xgb_tfidf_score])

XGBoost Regression TFIDF:  0.7703016241299304


## Building Classifiers - Word2Vec

In [ ]:
from gensim.models import Word2Vec

In [ ]:
content=X_train['content1'].values

In [ ]:
master_list=[]
for data in content:
  tmp_l=data.split()
  master_list.append(tmp_l)

In [ ]:
model = Word2Vec(master_list, window=5, min_count=1, workers=4)

In [ ]:
model

In [ ]:
#Getting Most Similar Words
model.wv.most_similar('anaconda')

[('prompt', 0.9966025948524475),
 ('pip', 0.9953254461288452),
 ('install', 0.9948974251747131),
 ('conda', 0.9938082695007324),
 ('tensorflow', 0.9937628507614136),
 ('error', 0.9933193922042847),
 ('installing', 0.9906993508338928),
 ('dell', 0.9906964302062988),
 ('notebook', 0.9906030297279358),
 ('getting', 0.9897632598876953)]

In [ ]:
model.save("word2vec.model")

In [ ]:
model = Word2Vec.load('word2vec.model')

In [ ]:
model.wv.vocab.keys()

dict_keys(['able', 'apply', 'internship', 'sir', 'please', 'provide', 'syllabus', 'dashboard', 'access', 'community', 'class', 'started', 'yesterday', 'thanks', 'thank', 'regarding', 'azure', 'chatbot', 'getting', 'error', 'installing', 'node', 'software', 'executing', 'app', 'j', 'file', 'hello', 'team', 'pyspark', 'session', 'today', 'cmd', 'dsa', 'important', 'data', 'science', 'career', 'clarify', 'doubt', 'join', 'send', 'payment', 'link', 'course', 'pls', 'get', 'dl', 'batch', 'u', 'start', 'giving', 'grade', 'hv', 'already', 'submitted', 'assignment', 'bt', 'received', 'predict', 'linear', 'regression', 'model', 'exception', 'message', 'module', 'named', 'sklearn', 'linear_model', '_base', 'hi', 'james', 'mlth', 'june', 'sumbit', 'challenge', 'code', 'name', 'read', 'csv', 'write', 'log', 'bcoz', 'unavailability', 'practice', 'part', 'current', 'also', 'tell', 'could', 'month', 'onsite', 'final', 'year', 'know', 'feasible', 'senarios', 'possible', 'inform', 'importing', 'tensorf

In [ ]:
word_vector=set(model.wv.vocab.keys())

In [ ]:
# we are converting a dictionary with word as a key, and the idf as a value
tfidf_dict = dict(zip(tfvec.get_feature_names(), list(tfvec.idf_)))
tfidf_words = set(tfvec.get_feature_names())

##### Weighted Word2Vec TFIDF Training Data

In [ ]:
# average Word2Vec
# compute average word2vec for each review.
tfidf_w2v_train = []; # the avg-w2v for each sentence/review is stored in this list
for sentence in tqdm(X_train['content1'].values): # for each review/sentence
    vector = np.zeros(100) # as word vectors are of zero length
    tf_idf_weight =0; # num of words with a valid vector in the sentence/review
    for word in sentence.split(): # for each word in a review/sentence
        if (word in word_vector) and (word in tfidf_words):
            vec = model.wv[word] # getting the vector for each word
            # here we are multiplying idf value(dictionary[word]) and the tf value((sentence.count(word)/len(sentence.split())))
            tf_idf = tfidf_dict[word]*(sentence.count(word)/len(sentence.split())) # getting the tfidf value for each word
            vector += (vec * tf_idf) # calculating tfidf weighted w2v
            tf_idf_weight += tf_idf
            #vector += vec
    if tf_idf_weight != 0:
        vector /= tf_idf_weight
    tfidf_w2v_train.append(vector)

print(len(tfidf_w2v_train))
print(len(tfidf_w2v_train[0]))

100%|██████████| 18101/18101 [00:01<00:00, 15925.14it/s]

18101
100


In [ ]:
print(len(tfidf_w2v_train))
print(len(tfidf_w2v_train[0]))

18101
100


##### Weighted Word2Vec TFIDF Test Data

In [ ]:
# average Word2Vec
# compute average word2vec for each review.
tfidf_w2v_test = []; # the avg-w2v for each sentence/review is stored in this list
for sentence in tqdm(X_test['content1'].values): # for each review/sentence
    vector = np.zeros(100) # as word vectors are of zero length
    tf_idf_weight =0; # num of words with a valid vector in the sentence/review
    for word in sentence.split(): # for each word in a review/sentence
        if (word in word_vector) and (word in tfidf_words):
            vec = model.wv[word] # getting the vector for each word
            #print(vec.shape)
            # here we are multiplying idf value(dictionary[word]) and the tf value((sentence.count(word)/len(sentence.split())))
            tf_idf = tfidf_dict[word]*(sentence.count(word)/len(sentence.split())) # getting the tfidf value for each word
            vector += (vec * tf_idf) # calculating tfidf weighted w2v
            tf_idf_weight += tf_idf
    if tf_idf_weight != 0:
        vector /= tf_idf_weight
    tfidf_w2v_test.append(vector)

print(len(tfidf_w2v_test))
print(len(tfidf_w2v_test[0]))

100%|██████████| 6034/6034 [00:00<00:00, 14272.58it/s]

6034
100


In [ ]:
print(len(tfidf_w2v_test))
print(len(tfidf_w2v_test[0]))

6034
100


In [ ]:
tfidf_w2v_train_np=np.array(tfidf_w2v_train)
print(tfidf_w2v_train_np.shape)

(18101, 100)


In [ ]:
tfidf_w2v_test_np=np.array(tfidf_w2v_test)
print(tfidf_w2v_test_np.shape)

(6034, 100)


In [ ]:
print(type(X_train_polarity_norm))
print(type(tfidf_w2v_train_np))

<class 'numpy.ndarray'>
<class 'numpy.ndarray'>


In [ ]:
X_train_polarity_norm.shape

(18101, 1)

#### Logistic Regression

In [ ]:
log_w2v_score=model_logisticregression(tfidf_w2v_train_np,y_train,tfidf_w2v_test_np,y_test)
print('Logistic Regression Gensim Word2Vec: ', log_w2v_score)
data_list.append(['Gensim Word2Vec','Logistic Regression',log_w2v_score])

0.4937023533311236
Logistic Regression Gensim Word2Vec:  0.4937023533311236


#### DecisionTree Regression

In [ ]:
decision_w2v_score=model_decisionregression(tfidf_w2v_train_np,y_train,tfidf_w2v_test_np,y_test)
print('Decision Tree Regression Gensim Word2Vec: ', decision_w2v_score)
data_list.append(['Gensim Word2Vec','DecisionTree Regression',decision_w2v_score])

Decision Tree Regression Gensim Word2Vec:  0.5137553861451774


#### RandomForest Regression

In [ ]:
rf_w2v_score=model_rfregression(tfidf_w2v_train_np,y_train,tfidf_w2v_test_np,y_test)
print('RandomForest Regression Gensim Word2Vec: ', rf_w2v_score)
data_list.append(['Gensim Word2Vec','RandomForest Regression',rf_w2v_score])

RandomForest Regression Gensim Word2Vec:  0.5772290354656944


#### XGBoost Regression

In [ ]:
xgb_w2v_score=model_xgbregression(tfidf_w2v_train_np,y_train,tfidf_w2v_test_np,y_test)
print('XGBoost Regression Gensim Word2Vec: ', xgb_w2v_score)
data_list.append(['Gensim Word2Vec','XGBoost Regression',xgb_w2v_score])

XGBoost Regression Gensim Word2Vec:  0.573417301955585


## Glove Implementation

##### Downloading Glove Model

In [ ]:
!wget https://nlp.stanford.edu/data/wordvecs/glove.42B.300d.zip

--2021-06-16 16:47:32--  https://nlp.stanford.edu/data/wordvecs/glove.42B.300d.zip
Resolving nlp.stanford.edu (nlp.stanford.edu)... 171.64.67.140
Connecting to nlp.stanford.edu (nlp.stanford.edu)|171.64.67.140|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: http://downloads.cs.stanford.edu/nlp/data/wordvecs/glove.42B.300d.zip [following]
--2021-06-16 16:47:33--  http://downloads.cs.stanford.edu/nlp/data/wordvecs/glove.42B.300d.zip
Resolving downloads.cs.stanford.edu (downloads.cs.stanford.edu)... 171.64.64.22
Connecting to downloads.cs.stanford.edu (downloads.cs.stanford.edu)|171.64.64.22|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1877802108 (1.7G) [application/zip]
Saving to: ‘glove.42B.300d.zip’

glove.42B.300d.zip  100%[===================>]   1.75G  4.94MB/s    in 5m 58s  

2021-06-16 16:53:31 (5.00 MB/s) - ‘glove.42B.300d.zip’ saved [1877802108/1877802108]



In [ ]:
!unzip glove*.zip

Archive:  glove.42B.300d.zip
  inflating: glove.42B.300d.txt      


##### Creating Custom Glove Model For Words Present in the dataset

In [ ]:
def loadGloveModel(gloveFile):
    print ("Loading Glove Model")
    f = open(gloveFile,'r', encoding="utf8")
    model = {}
    for line in tqdm(f):
        splitLine = line.split()
        word = splitLine[0]
        embedding = np.array([float(val) for val in splitLine[1:]])
        model[word] = embedding
    print ("Done.",len(model)," words loaded!")
    return model
model = loadGloveModel('glove.42B.300d.txt')

948it [00:00, 9478.99it/s]

Loading Glove Model


1917495it [03:17, 9702.24it/s]

Done. 1917495  words loaded!


In [ ]:
type(list(X_train['content1'].values))

preproced_texts=list(X_train['content1'].values)

In [ ]:
words = []
for i in preproced_texts:
    words.extend(i.split(' '))

print("all the words in the coupus", len(words))
words = set(words)
print("the unique words in the coupus", len(words))

inter_words = set(model.keys()).intersection(words)
print("The number of words that are present in both glove vectors and our coupus", \
      len(inter_words),"(",np.round(len(inter_words)/len(words)*100,3),"%)")

words_courpus = {}
words_glove = set(model.keys())
for i in words:
    if i in words_glove:
        words_courpus[i] = model[i]
print("word 2 vec length", len(words_courpus))


# stronging variables into pickle files python: http://www.jessicayung.com/how-to-use-pickle-to-save-and-load-variables-in-python/

import pickle
with open('glove_vectors', 'wb') as f:
    pickle.dump(words_courpus, f)

all the words in the coupus 109049
the unique words in the coupus 7767
The number of words that are present in both glove vectors and our coupus 6055 ( 77.958 %)
word 2 vec length 6055


##### Creating Glove Word2Vec Train Dataset.

In [ ]:
# make sure you have the glove_vectors file
with open('glove_vectors', 'rb') as f:
    model = pickle.load(f)
    glove_words =  set(model.keys())

In [ ]:
# Glove
# compute Glove for each query.
avg_glove_train = []; # the Glove for each sentence/review is stored in this list
for sentence in tqdm(X_train['content1'].values): # for each review/sentence
    vector = np.zeros(300) # as word vectors are of zero length
    cnt_words =0;
    for word in sentence.split():
        if word in glove_words:
            vector += model[word] # getting the vector for each word
            cnt_words += 1
    if cnt_words != 0:
        vector /= cnt_words
    avg_glove_train.append(vector)

print(len(avg_glove_train))
print(len(avg_glove_train[0]))

100%|██████████| 18101/18101 [00:00<00:00, 57811.57it/s]

18101
300


##### Creating Glove Word2Vec Test Dataset.

In [ ]:
# Glove
# compute Glove for each query.
avg_glove_test = []; # the Glove for each sentence/review is stored in this list
for sentence in tqdm(X_test['content1'].values): # for each review/sentence
    vector = np.zeros(300) # as word vectors are of zero length
    cnt_words =0;
    for word in sentence.split():
        if word in glove_words:
            vector += model[word] # getting the vector for each word
            cnt_words += 1
    if cnt_words != 0:
        vector /= cnt_words
    avg_glove_test.append(vector)

print(len(avg_glove_test))
print(len(avg_glove_test[0]))

100%|██████████| 6034/6034 [00:00<00:00, 58488.74it/s]

6034
300


#### Logistic Regression

In [ ]:
log_glove_score=model_logisticregression(avg_glove_train,y_train,avg_glove_test,y_test)
print('Logistic Regression Glove Word2Vec: ', log_glove_score)
data_list.append(['Glove Word2Vec','Logistic Regression',log_glove_score])

0.766489890619821
Logistic Regression Glove Word2Vec:  0.766489890619821


#### DecisionTree Regression

In [ ]:
decision_glove_score=model_decisionregression(avg_glove_train,y_train,avg_glove_test,y_test)
print('Decision Tree Regression Glove Word2Vec: ', decision_glove_score)
data_list.append(['Glove Word2Vec','DecisionTree Regression',decision_glove_score])

Decision Tree Regression Glove Word2Vec:  0.5129267484255884


#### RandomForest Regression

In [ ]:
rf_glove_score=model_rfregression(avg_glove_train,y_train,avg_glove_test,y_test)
print('RandomForest Regression Glove Word2Vec: ', rf_glove_score)
data_list.append(['Glove Word2Vec','RandomForest Regression',rf_glove_score])

RandomForest Regression Glove Word2Vec:  0.6736824660258535


#### XGBoost Regression

In [ ]:
xgb_glove_score=model_xgbregression(np.array(avg_glove_train),y_train,np.array(avg_glove_test),y_test)
print('XGBoost Regression Glove Word2Vec: ', xgb_glove_score)
data_list.append(['Glove Word2Vec','XGBoost Regression',xgb_glove_score])

XGBoost Regression Glove Word2Vec:  0.7194232681471661


In [ ]:
data_list

[['Bag Of Words', 'Logistic Regression', 0.7726218097447796],
 ['Bag Of Words', 'DecisionTree Regression', 0.7185946304275771],
 ['Bag Of Words', 'RandomForest Regression', 0.7434537620152469],
 ['Bag Of Words', 'XGBoost Regression', 0.7765992707988068],
 ['TF-IDF', 'Logistic Regression', 0.7444481272787538],
 ['TF-IDF', 'DecisionTree Regression', 0.7263838249917136],
 ['TF-IDF', 'RandomForest Regression', 0.7621809744779582],
 ['TF-IDF', 'XGBoost Regression', 0.7703016241299304],
 ['Gensim Word2Vec', 'Logistic Regression', 0.4937023533311236],
 ['Gensim Word2Vec', 'DecisionTree Regression', 0.5137553861451774],
 ['Gensim Word2Vec', 'RandomForest Regression', 0.5772290354656944],
 ['Gensim Word2Vec', 'XGBoost Regression', 0.573417301955585],
 ['Glove Word2Vec', 'Logistic Regression', 0.766489890619821],
 ['Glove Word2Vec', 'DecisionTree Regression', 0.5129267484255884],
 ['Glove Word2Vec', 'RandomForest Regression', 0.6736824660258535],
 ['Glove Word2Vec', 'XGBoost Regression', 0.71942

In [ ]:
df_pred=pd.DataFrame(data_list,columns=['Vectorizer','Model Name','Score'])

In [ ]:
df_pred

Vectorizer               Model Name     Score
0      Bag Of Words      Logistic Regression  0.772622
1      Bag Of Words  DecisionTree Regression  0.718595
2      Bag Of Words  RandomForest Regression  0.743454
3      Bag Of Words       XGBoost Regression  0.776599
4            TF-IDF      Logistic Regression  0.744448
5            TF-IDF  DecisionTree Regression  0.726384
6            TF-IDF  RandomForest Regression  0.762181
7            TF-IDF       XGBoost Regression  0.770302
8   Gensim Word2Vec      Logistic Regression  0.493702
9   Gensim Word2Vec  DecisionTree Regression  0.513755
10  Gensim Word2Vec  RandomForest Regression  0.577229
11  Gensim Word2Vec       XGBoost Regression  0.573417
12   Glove Word2Vec      Logistic Regression  0.766490
13   Glove Word2Vec  DecisionTree Regression  0.512927
14   Glove Word2Vec  RandomForest Regression  0.673682
15   Glove Word2Vec       XGBoost Regression  0.719423

## Final Accuracy Scores

In [ ]:
from prettytable import PrettyTable

In [ ]:
from tabulate import tabulate

In [ ]:
print(tabulate(df_pred, headers='keys', tablefmt='psql'))

+----+-----------------+-------------------------+----------+
|    | Vectorizer      | Model Name              |    Score |
|----+-----------------+-------------------------+----------|
|  0 | Bag Of Words    | Logistic Regression     | 0.772622 |
|  1 | Bag Of Words    | DecisionTree Regression | 0.718595 |
|  2 | Bag Of Words    | RandomForest Regression | 0.743454 |
|  3 | Bag Of Words    | XGBoost Regression      | 0.776599 |
|  4 | TF-IDF          | Logistic Regression     | 0.744448 |
|  5 | TF-IDF          | DecisionTree Regression | 0.726384 |
|  6 | TF-IDF          | RandomForest Regression | 0.762181 |
|  7 | TF-IDF          | XGBoost Regression      | 0.770302 |
|  8 | Gensim Word2Vec | Logistic Regression     | 0.493702 |
|  9 | Gensim Word2Vec | DecisionTree Regression | 0.513755 |
| 10 | Gensim Word2Vec | RandomForest Regression | 0.577229 |
| 11 | Gensim Word2Vec | XGBoost Regression      | 0.573417 |
| 12 | Glove Word2Vec  | Logistic Regression     | 0.76649  |
| 13 | G